In [6]:
import pandas as pd
import os

from helpers import (
    get_combined_df,
    save_final_df_as_jsonl,
    handle_slug_column_mappings,
    set_home_type,
)

In [7]:
DATA_DIR = "../data"
PROCESSED_DIR = "../processed/"
FACET_DIR = "days_on_market/"
FULL_DATA_DIR_PATH = os.path.join(DATA_DIR, FACET_DIR)
FULL_PROCESSED_DIR_PATH = os.path.join(PROCESSED_DIR, FACET_DIR)

In [8]:
data_frames = []

exclude_columns = [
    "RegionID",
    "SizeRank",
    "RegionName",
    "RegionType",
    "StateName",
    "Home Type",
]

slug_column_mappings = {
    "_mean_listings_price_cut_amt_": "Mean Listings Price Cut Amount",
    "_med_doz_pending_": "Median Days on Pending",
    "_median_days_to_pending_": "Median Days to Close",
    "_perc_listings_price_cut_": "Percent Listings Price Cut",
}


for filename in os.listdir(FULL_DATA_DIR_PATH):
    if filename.endswith(".csv"):
        print("processing " + filename)
        # skip month files for now since they are redundant
        if "month" in filename:
            continue

        cur_df = pd.read_csv(os.path.join(FULL_DATA_DIR_PATH, filename))

        cur_df["RegionName"] = cur_df["RegionName"].astype(str)
        cur_df = set_home_type(cur_df, filename)

        data_frames = handle_slug_column_mappings(
            data_frames, slug_column_mappings, exclude_columns, filename, cur_df
        )


combined_df = get_combined_df(
    data_frames,
    [
        "RegionID",
        "SizeRank",
        "RegionName",
        "RegionType",
        "StateName",
        "Home Type",
        "Date",
    ],
)

combined_df

processing Metro_med_listings_price_cut_amt_uc_sfr_month.csv
processing Metro_perc_listings_price_cut_uc_sfr_week.csv
processing Metro_med_listings_price_cut_amt_uc_sfrcondo_month.csv
processing Metro_med_listings_price_cut_amt_uc_sfr_week.csv
processing Metro_med_doz_pending_uc_sfrcondo_month.csv
processing Metro_mean_listings_price_cut_amt_uc_sfr_sm_month.csv
processing Metro_med_listings_price_cut_perc_uc_sfrcondo_sm_month.csv
processing Metro_mean_days_to_close_uc_sfrcondo_week.csv
processing Metro_mean_days_to_close_uc_sfrcondo_month.csv
processing Metro_mean_listings_price_cut_amt_uc_sfrcondo_sm_month.csv
processing Metro_med_listings_price_cut_perc_uc_sfr_week.csv
processing Metro_median_days_to_close_uc_sfrcondo_sm_week.csv
processing Metro_med_listings_price_cut_perc_uc_sfr_sm_week.csv
processing Metro_mean_listings_price_cut_perc_uc_sfrcondo_sm_week.csv
processing Metro_perc_listings_price_cut_uc_sfrcondo_week.csv
processing Metro_med_doz_pending_uc_sfrcondo_sm_month.csv
proc

In [4]:
# Adjust column names
final_df = combined_df.rename(
    columns={
        "RegionID": "Region ID",
        "SizeRank": "Size Rank",
        "RegionName": "Region",
        "RegionType": "Region Type",
        "StateName": "State",
    }
)

final_df["Date"] = pd.to_datetime(final_df["Date"], format="%Y-%m-%d")

final_df

Region ID  Size Rank         Region Region Type State  Home Type  \
0          102001          0  United States     country   NaN        SFR   
1          102001          0  United States     country   NaN        SFR   
2          102001          0  United States     country   NaN        SFR   
3          102001          0  United States     country   NaN        SFR   
4          102001          0  United States     country   NaN        SFR   
...           ...        ...            ...         ...   ...        ...   
586709     845172        769   Winfield, KS         msa    KS  all homes   
586710     845172        769   Winfield, KS         msa    KS  all homes   
586711     845172        769   Winfield, KS         msa    KS  all homes   
586712     845172        769   Winfield, KS         msa    KS  all homes   
586713     845172        769   Winfield, KS         msa    KS  all homes   

             Date  Percent Listings Price Cut  Mean Listings Price Cut Amount  \
0      2018-01-06                         NaN                    13508.368375   
1      2018-01-13                    0.049042                    14114.788383   
2      2018-01-20                    0.044740                    14326.128956   
3      2018-01-27                    0.047930                    13998.585612   
4      2018-02-03                    0.047622                    14120.035549   
...           ...                         ...                             ...   
586709 2024-01-06                    0.094017                             NaN   
586710 2024-01-13                    0.070175                             NaN   
586711 2024-01-20                    0.043478                             NaN   
586712 2024-01-27                    0.036697                             NaN   
586713 2024-02-03                    0.077670                             NaN   

        Percent Listings Price Cut (Smoothed)  \
0                                         NaN   
1                                         NaN   
2                                         NaN   
3                                         NaN   
4                                    0.047622   
...                                       ...   
586709                               0.037378   
586710                               0.043203   
586711                               0.054073   
586712                               0.061092   
586713                               0.057005   

        Mean Listings Price Cut Amount (Smoothed)  \
0                                             NaN   
1                                             NaN   
2                                             NaN   
3                                    13998.585612   
4                                    14120.035549   
...                                           ...   
586709                                        NaN   
586710                                        NaN   
586711                                        NaN   
586712                                        NaN   
586713                                        NaN   

        Median Days on Pending (Smoothed)  Median Days on Pending  
0                                     NaN                     NaN  
1                                     NaN                     NaN  
2                                     NaN                     NaN  
3                                     NaN                     NaN  
4                                     NaN                     NaN  
...                                   ...                     ...  
586709                                NaN                     NaN  
586710                                NaN                     NaN  
586711                                NaN                     NaN  
586712                                NaN                     NaN  
586713                                NaN                     NaN  

[586714 rows x 13 columns]

In [5]:
save_final_df_as_jsonl(FULL_PROCESSED_DIR_PATH, final_df)